<h2>Introduction</h2>

Paris is the capital and largest city of France and the capital of the Île-de-France region. It is the political and cultural center of France. It has 20 districts conjugated according to its development history. There have been no major changes since the 1860s. As of 2011, the population of Paris is more than 2.25 million, and the population of the Paris metropolitan area is more than 12.29 million, which is one of the largest metropolitan areas in Europe. Paris is the largest urban economy in Europe and the sixth largest urban economy in the world. All this brings fierce competition.
 

<h2>Business problem</h2>
How can it bring an advantage to an unknown restaurant with the location? I think 2 points are very important
1st:There are enough customers around him
In this question, we will assume that the main source of customers comes from schools and companies. At the same time, the convenient announcement traffic can also make the restaurant have more passenger flow
2nd:Competition around will not be very fierce


In [1]:
!conda install -c conda-forge pyproj
import pandas as pd
import numpy as np
import requests
!conda install -c conda-forge folium=0.5.0 --yes
import folium
import pyproj
!conda install -c conda-forge geopy
from geopy.geocoders import Nominatim
import math
from folium.plugins import HeatMap, Fullscreen
from sklearn.cluster import KMeans

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - pyproj


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    certifi-2020.6.20          |   py36h9f0ad1d_0         151 KB  conda-forge
    proj-7.0.0                 |       h5a2d94f_2         3.7 MB  conda-forge
    openssl-1.1.1g             |       h516909a_0         2.1 MB  conda-forge
    krb5-1.16.4                |       h173b8e3_0         1.4 MB
    python_abi-3.6             |          1_cp36m           4 KB  conda-forge
    pyproj-2.6.1.post1         |   py36he34cbb8_0         426 KB  conda-forge
    curl-7.68.0                |       hf8cf82a_0         137 KB  conda-forge
    libcurl-7.68.0             |       hda55be3_0         564 KB  conda-forge
    ca-certificates-2020.6.20  |       hecda079_0         145 KB  conda-forge
    -------------------------

<h2>Data preparetion</h2>

In [2]:
address = 'Saint-Michel,75005,FR'
geolocator = Nominatim(user_agent="paris_explorer")
g = geolocator.geocode(address)
paris_lat = g.latitude
paris_lon = g.longitude
print('The coordinate of the center of Paris are {}, {}.'.format(paris_lat, paris_lon))
print('With its address : {}'.format(geolocator.reverse((paris_lat, paris_lon))))

The coordinate of the center of Paris are 48.8532188, 2.3458645.
With its address : Saint-Michel, Rue Xavier Privas, Îlot Saint-Séverin, Quartier de la Sorbonne, Paris, Île-de-France, France métropolitaine, 75005, France


*we want to calculate the distance with all the restaurant we can found, to do so we need to convert our latitudes and longitudes to Cartesian coordinate*

In [3]:
def to_xy(lat, lon):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=31, datum='WGS84')
    xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
    return xy[0], xy[1]

def to_latlon(x, y):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=31, datum='WGS84')
    lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
    return lonlat[1], lonlat[0]

def calc_distance(x1, y1, x2, y2):
    dx = x2 - x1
    dy = y2 - y1
    return math.sqrt(dx*dx + dy*dy)


In [4]:
def get_areas():
    
    latitudes = []
    longitudes = []
    Xs=[]
    Ys=[]
    distances=[]
    paris_x, paris_y = to_xy(paris_lat, paris_lon)

    min_x = int(paris_x - 6000)
    max_x = int(paris_x + 5000)
    min_y = int(paris_y - 3500)
    max_y = int(paris_y + 5500)
    radius=700
    for x in range(min_x, max_x, radius):
        for y in range(min_y, max_y, radius):
            
            d = calc_distance(paris_x, paris_y, x, y)
            if d <= 6000:
                
                lat, lon = to_latlon(x, y)
                longitudes.append(lon)
                latitudes.append(lat)
                Xs.append(x)
                Ys.append(y)
                distances.append(d)
    return latitudes, longitudes,Xs,Ys,distances
            


In [5]:
import warnings
warnings.simplefilter("ignore")

In [6]:
latitudes,longitudes,xs,ys,distances=get_areas()

In [7]:

map_paris = folium.Map(location=[paris_lat,paris_lon], zoom_start=12)
folium.Marker([paris_lat,paris_lon], popup='starter').add_to(map_paris)
for lat, lon in zip(latitudes, longitudes):
    folium.Circle([lat, lon], radius=350, color='blue', fill=False).add_to(map_paris)
map_paris

In [8]:
 df_locations = pd.DataFrame({'Latitude': latitudes,
                              'Longitude': longitudes,
                              'X': xs,
                              'Y': ys,
                              'Distance from center': distances})
df_locations.head()

Latitude  Longitude       X        Y  Distance from center
0  48.827597   2.273977  446714  5408545           5994.815592
1  48.833894   2.273886  446714  5409245           5701.526324
2  48.840190   2.273795  446714  5409945           5482.425637
3  48.846487   2.273704  446714  5410645           5346.641872
4  48.852784   2.273613  446714  5411345           5300.581831

In [9]:
df_locations.columns= ['Neighborhood Latitude','Neighborhood Longitude','X','Y','Distance from center']

In [10]:
CLIENT_ID = 'DT21RPMCEHJUMGX1MNEXPV1EPEWZGBNOO0ZOAYJYXOEKPCT5' 
CLIENT_SECRET = 'DRSAEMH2MZT3FFRPULUXQLKK0BRQJJPEWBHHM0KLRRSECYLG' 
VERSION = '20180605' 
RADIUS = 350
LIMIT=100

In [27]:
CLIENT_ID = 'RWXUUUOHJT04GQOAPAZJPFZWEQIMB2RFS4WSW4B13JCYDNEJ' 
CLIENT_SECRET = 'FTLLE13ICYVULTHUMA5HNIXMNM21YOROZSF1PXQE0TMERMRX' 

In [11]:
restaurant_category = '4d4b7105d754a06374d81259'
asian_category='4bf58dd8d48988d142941735'

In [12]:
def get_nearby_venues(latitudes, longitudes,category):
    
    
    venues_list = []
    
    for lat, lng in zip(latitudes, longitudes):
        url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&categoryId={}&radius={}&limit={}'.format(
        CLIENT_ID, CLIENT_SECRET, VERSION, lat, lng, category, RADIUS,LIMIT)
        try:
            results = requests.get(url).json()['response']['groups'][0]['items']
            venues_list.append([(
                       lat, 
                       lng, 
                       item['venue']['name'],
                       item['venue']['categories'][0]['name'],
                       item['venue']['location']['lat'], 
                       item['venue']['location']['lng'],
                       format_address(item['venue']['location'])) for item in results])  
        except:
            pass
            
    nearby_venues= pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Name', 
                  'Category',           
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Address' 
                  ]
    return(nearby_venues)    

In [13]:
def format_address(location):
    address = ', '.join(location['formattedAddress'])
    return address

In [14]:
url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&categoryId={}&radius={}&limit={}'.format(
        CLIENT_ID, CLIENT_SECRET, VERSION,48.827597,2.273977, asian_category, RADIUS,LIMIT)
print(url)
#it's only for test if your client credentials is still valable

https://api.foursquare.com/v2/venues/explore?client_id=DT21RPMCEHJUMGX1MNEXPV1EPEWZGBNOO0ZOAYJYXOEKPCT5&client_secret=DRSAEMH2MZT3FFRPULUXQLKK0BRQJJPEWBHHM0KLRRSECYLG&v=20180605&ll=48.827597,2.273977&categoryId=4bf58dd8d48988d142941735&radius=350&limit=100


In [15]:
paris_restaurant_data = get_nearby_venues(latitudes, longitudes,asian_category)

In [16]:
paris_restaurant_data.head()

Neighborhood Latitude  Neighborhood Longitude        Name  \
0              48.827597                2.273977  Chuan Yang   
1              48.827597                2.273977       E-ban   
2              48.827597                2.273977  Sushi Fuji   
3              48.827597                2.273977    Fujiyama   
4              48.840190                2.273795       Koedo   

              Category  Venue Latitude  Venue Longitude  \
0     Asian Restaurant       48.824834         2.271726   
1    Korean Restaurant       48.826264         2.273570   
2     Sushi Restaurant       48.826220         2.273485   
3  Japanese Restaurant       48.827891         2.275762   
4  Japanese Restaurant       48.839498         2.271406   

                                             Address  
0    13 rue Hoche, 92130 Issy-les-Moulineaux, France  
1  14 avenu de la République, Issy-les-Moulineaux...  
2  14 avenue de la République, 92130 Issy-les-Mou...  
3  3 bis rue Henri Mayer, 92130 Issy-les-Moulinea...  
4   Gare RER Pont Du Garigliano, 75015 Paris, France

In [20]:
paris_restaurant_data.shape

(1628, 7)

In [17]:
paris_restaurant_data['Category'].unique()

array(['Asian Restaurant', 'Korean Restaurant', 'Sushi Restaurant',
       'Japanese Restaurant', 'Chinese Restaurant', 'Thai Restaurant',
       'Vietnamese Restaurant', 'Noodle House', 'Cambodian Restaurant',
       'Indian Restaurant', 'Cantonese Restaurant', 'French Restaurant',
       'Bagel Shop', 'Udon Restaurant', 'Massage Studio', 'Café',
       'Indonesian Restaurant', 'Tea Room', 'Mediterranean Restaurant',
       'Shabu-Shabu Restaurant', 'Lounge', 'Sandwich Place',
       'Ramen Restaurant', 'Soba Restaurant', 'Dim Sum Restaurant',
       'Szechuan Restaurant', 'Restaurant', 'Bistro',
       'Tibetan Restaurant', 'Seafood Restaurant', 'Brasserie',
       'Taiwanese Restaurant', 'Karaoke Bar', 'Snack Place',
       'Shandong Restaurant', 'Bakery', 'Okonomiyaki Restaurant',
       'Shanxi Restaurant', 'BBQ Joint', 'Fish Market', 'Coffee Shop',
       'Vegetarian / Vegan Restaurant', 'Spa', 'Halal Restaurant',
       'Jiangxi Restaurant'], dtype=object)

In [18]:
not_restaurant=['Bagel Shop','Massage Studio','Café','Tea Room','Lounge', 'Sandwich Place','Bistro','Brasserie','Karaoke Bar', 'Snack Place','Bakery','BBQ Joint', 'Fish Market', 'Coffee Shop','Spa']

In [19]:

restaurant_asian_paris = paris_restaurant_data[~paris_restaurant_data['Category'].isin(not_restaurant)].reset_index(drop = True)
restaurant_asian_paris.head()

Neighborhood Latitude  Neighborhood Longitude        Name  \
0              48.827597                2.273977  Chuan Yang   
1              48.827597                2.273977       E-ban   
2              48.827597                2.273977  Sushi Fuji   
3              48.827597                2.273977    Fujiyama   
4              48.840190                2.273795       Koedo   

              Category  Venue Latitude  Venue Longitude  \
0     Asian Restaurant       48.824834         2.271726   
1    Korean Restaurant       48.826264         2.273570   
2     Sushi Restaurant       48.826220         2.273485   
3  Japanese Restaurant       48.827891         2.275762   
4  Japanese Restaurant       48.839498         2.271406   

                                             Address  
0    13 rue Hoche, 92130 Issy-les-Moulineaux, France  
1  14 avenu de la République, Issy-les-Moulineaux...  
2  14 avenue de la République, 92130 Issy-les-Mou...  
3  3 bis rue Henri Mayer, 92130 Issy-les-Moulinea...  
4   Gare RER Pont Du Garigliano, 75015 Paris, France

In [25]:
restaurant_asian_paris = restaurant_asian_paris.drop_duplicates('Venue Longitude')

In [21]:
japanese_restaurant_paris = restaurant_asian_paris[restaurant_asian_paris['Category']=='Japanese Restaurant']
restaurant_position = [[lat, lon] for lat, lon in zip(restaurant_asian_paris['Venue Latitude'], restaurant_asian_paris['Venue Longitude'])]

*drop these which aren't restaurant,and remove those duplicates by their longitude*

In [22]:
map_restaurant = folium.Map(location=[paris_lat,paris_lon], zoom_start = 13)
HeatMap(restaurant_position).add_to(map_restaurant)
Fullscreen().add_to(map_restaurant)
map_restaurant.save('paris_japanses_restaurant.html')
map_restaurant

Let's take a look at the distribution of all restaurants

In [23]:
college_category ='4d4b7105d754a06372d81259'
travel_category='4d4b7105d754a06379d81259'
profession_category='4d4b7105d754a06375d81259'

In [24]:
paris_college_data = get_nearby_venues(latitudes, longitudes,college_category)

In [25]:
college_position = [[lat, lon] for lat, lon in zip(paris_college_data['Venue Latitude'], paris_college_data['Venue Longitude'])]

In [26]:
map_college= folium.Map(location=[paris_lat,paris_lon], zoom_start = 13)
HeatMap(college_position).add_to(map_college)
Fullscreen().add_to(map_college)
map_college.save('paris_college.html')
map_college

here shows the distribution of colleges

In [30]:
paris_college_data.head(10)

Neighborhood Latitude  Neighborhood Longitude  \
0              48.827597                2.273977   
1              48.827597                2.273977   
2              48.827597                2.273977   
3              48.827597                2.273977   
4              48.827597                2.273977   
5              48.827597                2.273977   
6              48.833894                2.273886   
7              48.833894                2.273886   
8              48.840190                2.273795   
9              48.846487                2.273704   

                                  Name                   Category  \
0         Ecole de Cuisine au Barbecue       College & University   
1  Digital Academy BDDF RH BNP Paribas                 University   
2                        Eurosae Paris  College Academic Building   
3      O.G.E.C. la Salle-Saint Nicolas              Middle School   
4                    Laboratoire SENSE                College Lab   
5                   Gymnase St Nicolas                College Gym   
6                                  EFB  College Academic Building   
7                             Gymboree                College Gym   
8                                PARCC                College Lab   
9                                 Isth          College Classroom   

   Venue Latitude  Venue Longitude  \
0       48.826839         2.270193   
1       48.827824         2.275609   
2       48.829350         2.275455   
3       48.826635         2.275998   
4       48.825415         2.275715   
5       48.825927         2.276093   
6       48.834717         2.271184   
7       48.833483         2.276682   
8       48.838045         2.274590   
9       48.847579         2.273275   

                                             Address  
0                        Issy-les-Moulineaux, France  
1                2 rue Laffitte, 75009 Paris, France  
2                                             France  
3  19 Rue Victor Hugo, 92130 Issy-les-Moulineaux,...  
4  38 rue du Général Leclerc, 92130 Issy les Moul...  
5                        Issy-les-Moulineaux, France  
6           63 Rue De Charenton, 75012 Paris, France  
7                                             France  
8                56 Rue Leblanc, 75015 Paris, France  
9                                             France

In [28]:
paris_travel_data = get_nearby_venues(latitudes, longitudes,travel_category)

paris_profession_data = get_nearby_venues(latitudes, longitudes,profession_category)

In [46]:
paris_travel_data['Category'].unique()

array(['Hotel', 'Bus Stop', 'Bike Rental / Bike Share',
       'Rental Car Location', 'Heliport', 'Tram Station', 'Metro Station',
       'Boat or Ferry', 'Train Station', 'Resort', 'Bus Station',
       'Bed & Breakfast', 'Hostel', 'Intersection', 'Vacation Rental'],
      dtype=object)

 as we can see in the data of travel we have,we may assume some of them can be seen as the resources of Potential customers while some of them are transportation facilities,
 we'd better seperate them into diffierent group

In [31]:
cosumer_Resource = ['Hotel', 'Vacation Rental','Resort' ,'Hostel']
transportation_Facilities=['Bus Stop','Rental Car Location','Tram Station', 'Metro Station','Train Station','Bus Station']

In [35]:
potential_customers_data = paris_travel_data[paris_travel_data['Category'].isin(cosumer_Resource )].reset_index(drop = True)
transportation_facilities_data = paris_travel_data[paris_travel_data['Category'].isin(transportation_Facilities)].reset_index(drop = True)

In [34]:
potential_customers_data = pd.concat([potential_customers_data, paris_college_data],axis = 0)
potential_customers_data = pd.concat([potential_customers_data, paris_profession_data],axis = 0)

In [37]:
map_paris = folium.Map(location=[paris_lat,paris_lon], zoom_start=12)
folium.Marker([paris_lat,paris_lon], popup='starter').add_to(map_paris)
for index, row in potential_customers_data.iterrows():
    lat = row["Venue Latitude"]; lon = row["Venue Longitude"]
    color = 'green'
    label = '{}'.format(row["Name"])
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker([lat, lon], radius=3, color=color, fill=True, fill_color=color,                         
                        popup=label, fill_opacity=1, parse_html=False).add_to(map_paris)
for index, row in restaurant_asian_paris.iterrows():
    lat = row["Venue Latitude"]; lon = row["Venue Longitude"]
    color = 'red'
    label = '{}'.format(row["Name"])
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker([lat, lon], radius=3, color=color, fill=True, fill_color=color,                         
                        popup=label, fill_opacity=1, parse_html=False).add_to(map_paris)
for index, row in transportation_facilities_data.iterrows():
    lat = row["Venue Latitude"]; lon = row["Venue Longitude"]
    color = 'blue'
    label = '{}'.format(row["Name"])
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker([lat, lon], radius=3, color=color, fill=True, fill_color=color,                         
                        popup=label, fill_opacity=1, parse_html=False).add_to(map_paris)

map_paris


We try to use different colors to mark the existing restaurants, customers and transportation facilities, but Paris is a very developed city. This picture can't visually see the situation of each area

therefore, we need a resume of each region

In [38]:
count_restaurant_neigh=restaurant_asian_paris.groupby(['Neighborhood Latitude','Neighborhood Longitude']).count()
count_cosumer_neigh=potential_customers_data.groupby(['Neighborhood Latitude','Neighborhood Longitude']).count()
count_transport_neigh=transportation_facilities_data.groupby(['Neighborhood Latitude','Neighborhood Longitude']).count()

In [39]:
count_cosumer_neigh.shape

(159, 5)

In [40]:
resume_neigh = count_restaurant_neigh.loc[:,['Name']].reset_index()
resume_neigh=pd.merge(resume_neigh,count_cosumer_neigh.loc[:,['Category']].reset_index(),on=['Neighborhood Latitude','Neighborhood Longitude'] )
resume_neigh=pd.merge(resume_neigh,count_transport_neigh.loc[:,['Address']].reset_index(),on=['Neighborhood Latitude','Neighborhood Longitude'] )

resume_neigh.columns=['Neighborhood Latitude','Neighborhood Longitude','number of restaurants','number of potential customers','number of transportation facilities']
resume_neigh.fillna(0)
resume_neigh.head()

Neighborhood Latitude  Neighborhood Longitude  number of restaurants  \
0              48.821419                2.293139                      2   
1              48.821477                2.302675                      7   
2              48.821534                2.312210                      9   
3              48.821591                2.321746                      3   
4              48.821809                2.359889                     35   

   number of potential customers  number of transportation facilities  
0                              3                                    2  
1                              4                                    1  
2                              2                                    2  
3                              7                                    6  
4                              3                                    5

In [154]:
resume_neigh= resume_neigh[resume_neigh['number of restaurants']<resume_neigh['number of restaurants'].mean()]
resume_neigh= resume_neigh[resume_neigh['number of potential customers']>resume_neigh['number of potential customers'].mean()]
resume_neigh= resume_neigh[resume_neigh['number of transportation facilities']>resume_neigh['number of transportation facilities'].mean()]

we try to find the region that has less competitors and more potential clients

In [155]:
resume_neigh.shape
#we got 25 candidates for the location,we can run this programme again to find the most potential area

(25, 5)

In [156]:
resume_neigh= resume_neigh[resume_neigh['number of restaurants']<resume_neigh['number of restaurants'].mean()]
resume_neigh= resume_neigh[resume_neigh['number of potential customers']>resume_neigh['number of potential customers'].mean()]
resume_neigh= resume_neigh[resume_neigh['number of transportation facilities']>resume_neigh['number of transportation facilities'].mean()]
resume_neigh.shape

(4, 5)

we got only 4 this time, it's easier to make the decisions~ 

In [157]:
resume_neigh.head()

Neighborhood Latitude  Neighborhood Longitude  number of restaurants  \
23               48.828210                2.378883                      4   
59               48.846833                2.330946                      5   
99               48.865554                2.302063                      4   
124              48.878030                2.282795                      4   

     number of potential customers  number of transportation facilities  
23                              41                                    6  
59                              50                                    9  
99                              50                                    6  
124                             45                                    6

<h2>Result:

In [42]:
final_latitude = [48.828210,48.846833,48.865554,48.878030]
final_longitude = [2.378883,2.330946,2.302063,2.282795]

In [43]:
map_paris_final_location = folium.Map(location=[paris_lat,paris_lon], zoom_start=12)
folium.Marker([paris_lat,paris_lon], popup='starter').add_to(map_paris_final_location)
for lat, lon in zip(final_latitude, final_longitude):
    folium.Circle([lat, lon], radius=350, color='blue', fill=False).add_to(map_paris_final_location)
map_paris_final_location

The circle shown in this picture are the best location to open a restaurant,but it's only based on the analysis of some aspect that i suggestd

In [46]:
for lat, lng in zip(final_latitude, final_longitude ):
    print('The neighboorhood address for restaurant : {}'.format(geolocator.reverse((lat, lng))))

The neighboorhood address for restaurant : Quartier de la Gare, Paris, Île-de-France, France métropolitaine, 75013, France
The neighboorhood address for restaurant : 13, Rue de Fleurus, Paris 6e Arrondissement, Paris, Île-de-France, France métropolitaine, 75006, France
The neighboorhood address for restaurant : Sartore, 3, Avenue Montaigne, Quartier des Champs-Élysées, Paris, Île-de-France, France métropolitaine, 75008, France
The neighboorhood address for restaurant : Porte Maillot, Boulevard Thierry de Martel, Quartier des Ternes, Paris, Île-de-France, France métropolitaine, 75116, France
